# Topic Modeling

Akio Kakishima

### Sources

https://radimrehurek.com/gensim/models/ldaseqmodel.html

https://markroxor.github.io/gensim/static/notebooks/ldaseqmodel.html

https://www.youtube.com/watch?v=7BMsuyBPx90 <-- Dave Blei's Google talk on Dynamic Topic Modelling

https://towardsdatascience.com/exploring-the-un-general-debates-with-dynamic-topic-models-72dc0e307696 

^ Explains why each new paragraph should be treated as a separate document in DTM


### Notes
This .ipynb file runs topic modeling. Make sure to have parsed the PDFs before running this analysis. 

In [1]:
BIGRAMS = False
LOAD_DICTIONARY = True
LOAD_LDA = True
LOAD_DTM = False
num_topics = 15

In [2]:
from collections import Counter
from gensim import models
from gensim.corpora import Dictionary, bleicorpus
from gensim.models import ldaseqmodel, ldamodel
from gensim.models.wrappers.dtmmodel import DtmModel
from gensim.test.utils import datapath
import pyLDAvis
import matplotlib.pyplot as plt
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer 
import numpy as np
import os
import pandas as pd
import pickle
import re
import time
import winsound

C:\Users\Akio\Anaconda3\lib\site-packages\numpy\core\__init__.py:29: UserWarning: loaded more than 1 DLL from .libs:
C:\Users\Akio\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.CSRRD7HKRKC3T3YXA7VY7TAZGLSWDKW6.gfortran-win_amd64.dll
C:\Users\Akio\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.IPBC74C7KURV7CB2PKT5Z5FNR3SIBV4J.gfortran-win_amd64.dll
  stacklevel=1)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\utils.py:1209: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
C:\Users\Akio\Anaconda3\lib\site-packages\nltk\decorators.py:68: DeprecationWarning: `formatargspec` is deprecated since Python 3.5. Use `signature` and the `Signature` object directly
  regargs, varargs, varkwargs, defaults, formatvalue=lambda value: ""


In [3]:
def preprocess(raw, BIGRAM):
    """
    Takes in a string, lowercases all the text,
    fixes hyphenation, then tokenizes the input. 
    Outputs a list of all the tokens in the input document. 
    Each token is at least 3 chars long. 
    Also removed numbers, and stopwords. 
    Stopwords downloaded from nltk.downloads('stopwords'). 

    Parameters
    ----------
    first : string, or parser 
        `raw` is the pdf document

    Returns
    -------
    list
        A list of each token, stopword filtered

    """

    lowered = raw.lower()
    fixed = re.sub(r'[\-]\W+', '', lowered)
    whitespace = re.sub(r'[\W]+', ' ', fixed)

    tokenizer = RegexpTokenizer(r'[A-z]{4,}')
    additional_list = ['also', 'ndr', 'red', 'crescent', 'cross', 'world', 'disaster', 'report', 'chap', 'page']
    tokenized = [word for word in tokenizer.tokenize(fixed) if word not in additional_list]
    
    lemmatizer = WordNetLemmatizer()
    lemmed = [lemmatizer.lemmatize(word) for word in tokenized if word not in stopwords.words('english')]

    if BIGRAM:
        bigram = list(nltk.bigrams(lemmed))
        filtered_words = [i for i in map('_'.join, bigram)]
    else:
        filtered_words = lemmed
    
    return filtered_words

In [4]:
def extract_para(raw, len_list):
    """
    Input is lowercased, and split by paragraph breaks
    using regex. The number of paragraphs are analyzed
    and appended in input list, 'len_list'
    
    Returns a list, 'list_of_paragraphs', which is the
    output from the split function.

    Parameters
    ----------
    first : string
        text of the PDF file
    second : list
        list to keep track of number of paragraph 
        extracted from input, 'raw'
        
    Returns
    -------
    list

    """

    lowered = raw.lower()
    list_of_paragraphs = re.split(r'\.[ ][\n]+', lowered)
    len_list.append(len(list_of_paragraphs))
    
    return list_of_paragraphs

In [5]:
def determine_year(pdf_title):
    searchObj = re.search(r'20[0-9]{2}|19[0-9]{2}', pdf_title, re.M|re.I)
    if searchObj:
        year = searchObj.group()
    
    return int(year)

In [6]:
def beeper():
    '''
    Beeps when activated
    '''
    
    eighth = 250
    half = 1000
    g = 392 #hz
    ef = 311 #hz

    for i in range(3):
        winsound.Beep(g, eighth)
    winsound.Beep(ef, half)

## Get/Set common_corpus and common_dictionary

In [7]:
%%time

if LOAD_DICTIONARY:
    print("loading Dictionary, corpus, and len documents")
    common_dictionary = Dictionary.load('model/common_dictionary')
    with open('model/common_corpus_pickled', 'rb') as f:
        common_corpus = pickle.load(f)
    with open('model/len_docs_pickled', 'rb') as f:
        lengths_of_docs = pickle.load(f)
    
else:
    print("Dictionary, corpus, and len documents not found; initializing")

    text_library = {}
    list_of_string = []
    list_of_list_of_string = []
    lengths_of_docs = []

    path = "data/"
    dirs = os.listdir(path)
    for each_pdf in dirs:
        print(each_pdf)       
        with open('txt/{}.txt'.format(str(each_pdf)), 'r', encoding='utf8') as f:
            text = f.read()
            text_year = determine_year(each_pdf)
            try:
                text_update = "{}\n{}".format(text_library[text_year], text)
                text_library.update({text_year: text_update})
            except:
                text_library[text_year] = text

    for i in sorted(text_library):
        print("year: {}".format(i))
        text = text_library[i]
        list_of_paragraphs = extract_para(text, lengths_of_docs)
        for i in list_of_paragraphs:
            if len(i) > 3:
                list_of_list_of_string.append(preprocess(i, BIGRAMS))
            else: pass

    # Create a corpus from a list of texts
    common_dictionary = Dictionary(list_of_list_of_string)
    common_corpus = [common_dictionary.doc2bow(text) for text in list_of_list_of_string]

    common_dictionary.save('model/common_dictionary')
    with open('model/common_corpus_pickled', 'wb') as f:
        pickle.dump(common_corpus, f)
    with open('model/len_docs_pickled', 'wb') as f:
        pickle.dump(lengths_of_docs, f)

loading Dictionary, corpus, and len documents
Wall time: 114 ms


In [35]:
[print(i) for i in common_dictionary.values() if len(i) < 4]

act
aid
map
us
pay
ton
le
day
ngo
dy
dos
say
job
war
add
gun
get
aim
dot
fit
rat
box
bag
go
one
pas
net
kid
ten
way
bed
ass
gap
few
cut
lie
jar
kit
lid
arm
sum
cry
bee
boy
fee
ail
see
win
old
std
lot
son
dam
baa
tie
car
eye
run
fly
hit
sky
ray
cow
gas
peg
fix
lab
woe
bus
rom
ear
age
pub
sea
law
set
top
idp
lao
nrc
sam
buy
guy
leg
pot
pig
put
tap
end
can
key
ky
tax
dry
ant
toy
out
row
fad
me
rod
cc
ash
due
try
bar
pen
cap
gia
lay
dog
prc
tat
vac
ban
pit
jet
hus
sap
tip
web
hoe
ill
pat
jam
rug
doc
cob
pan
log
bos
egg
jaw
hut
hub
mat
pad
ebb
sin
vox
lee
yam
bog
sba
fig
nod
rag
ax
gay
lag
art
nun
plo
sex
nut
pea
ion
sub
tic
hug
ka
cop
fat
rim
tin
pms
fdr
rio
rot
i
nil
atm
oak
wei
wit
gee
dmd
tab
soh
bit
cue
pda
alp
let
bid
con
pro
isi
dad
mom
rut


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

## NMF

In [ ]:
# nmf = models.Nmf(common_corpus, num_topics=10)

## Baseline: LDA

In [12]:
%%time
home = os.getcwd()

if LOAD_LDA:
    print("loading LDAmodel")
    lda = ldamodel.LdaModel.load(os.path.join(home, 'model/LDAmodel_{}'.format(num_topics)))
else:
    for num_topics_sub in [5,10,15]:
        print("LDAmodel not found; initializing ldamodel")
        lda = ldamodel.LdaModel(corpus=common_corpus, id2word=common_dictionary, num_topics=num_topics_sub, update_every=1, passes=1)

        print("saving")
        lda.save(os.path.join(home, 'model/LDAmodel_{}'.format(num_topics_sub)))

loading LDAmodel
Wall time: 273 ms


In [13]:
def pretty_print_topic():
    epoch = []
    topic_list = []
    topic_imp = []
    
    for idx, each_topic in enumerate(lda.print_topics(num_topics=num_topics, num_words=len(common_dictionary.values()))):
        # len(common_dictionary.values()) = gets all vocab
        for each_token in each_topic[1].split('+'):
            topic_importance, token = each_token.split("*")
            topic_list.append(re.sub(r'[^A-z0-9]+', '', token))
            topic_imp.append(topic_importance)
            epoch.append(idx)
    data = {'epoch': epoch, 'topic': topic_list, 'topic_importance': topic_imp}
    lda_df = pd.DataFrame.from_dict(data)
#     print(len(lda_df))
#     display(lda_df)
    
    return lda_df

lda_df = pretty_print_topic()

for each_epoch in lda_df['epoch'].unique():
    display(lda_df[lda_df['epoch'] == each_epoch])

epoch          topic topic_importance
0          0   humanitarian            0.013
1          0         people            0.007
2          0  international            0.005
3          0   displacement            0.004
4          0   organization            0.004
5          0       response            0.004
6          0       rohingya            0.004
7          0    information            0.004
8          0          drone            0.004
9          0      available            0.004
10         0          human            0.004
11         0      emergency            0.004
12         0          right            0.004
13         0    development            0.003
14         0         system            0.003
15         0       disaster            0.003
16         0        country            0.003
17         0      community            0.003
18         0         agency            0.003
19         0           food            0.003
20         0           need            0.003
21         0        refugee            0.003
22         0         online            0.003
23         0         health            0.003
24         0          state            0.003
25         0           data            0.003
26         0           http            0.002
27         0       affected            0.002
28         0           help            0.002
29         0          group            0.002
...      ...            ...              ...
26247      0        shifang            0.000
26248      0        rocinha            0.000
26249      0       qionglai            0.000
26250      0     phenomenal            0.000
26251      0         peking            0.000
26252      0     noteworthy            0.000
26253      0         ington            0.000
26254      0           isco            0.000
26255      0          jakar            0.000
26256      0         karach            0.000
26257      0          kulna            0.000
26258      0     bangaldesh            0.000
26259      0           ampo            0.000
26260      0        tianjin            0.000
26261      0   surgeinduced            0.000
26262      0        shenzen            0.000
26263      0      rotterdam            0.000
26264      0         nagoya            0.000
26265      0           tati            0.000
26266      0        kolkata            0.000
26267      0      guangzhou            0.000
26268      0          tanbu            0.000
26269      0           ruhr            0.000
26270      0       randstad            0.000
26271      0           miam            0.000
26272      0          medel            0.000
26273      0           madr            0.000
26274      0           lcut            0.000
26275      0       haiphong            0.000
26276      0         acknow            0.000

[26277 rows x 3 columns]

epoch          topic topic_importance
26277      1   humanitarian            0.011
26278      1         people            0.009
26279      1  international            0.006
26280      1     protection            0.006
26281      1        society            0.005
26282      1       response            0.005
26283      1           blog            0.004
26284      1        country            0.004
26285      1       disaster            0.004
26286      1           need            0.004
26287      1       conflict            0.004
26288      1           risk            0.004
26289      1     government            0.004
26290      1        refugee            0.003
26291      1          right            0.003
26292      1      community            0.003
26293      1   organization            0.003
26294      1         agency            0.003
26295      1           many            0.003
26296      1        million            0.003
26297      1      principle            0.003
26298      1       affected            0.003
26299      1          child            0.003
26300      1       national            0.003
26301      1    information            0.003
26302      1          state            0.003
26303      1        chapter            0.003
26304      1     population            0.002
26305      1          local            0.002
26306      1         action            0.002
...      ...            ...              ...
52524      1     world_camp            0.000
52525      1        uniting            0.000
52526      1    risklandeng            0.000
52527      1   public_aware            0.000
52528      1         postpn            0.000
52529      1        veikoso            0.000
52530      1      final_pdf            0.000
52531      1        viekoso            0.000
52532      1           rcof            0.000
52533      1        jayanta            0.000
52534      1        othowai            0.000
52535      1        abdulla            0.000
52536      1     abdishakur            0.000
52537      1          tween            0.000
52538      1         tides]            0.000
52539      1         payout            0.000
52540      1          pated            0.000
52541      1          ensur            0.000
52542      1           crux            0.000
52543      1      confounds            0.000
52544      1         antici            0.000
52545      1     [unusually            0.000
52546      1     smallscale            0.000
52547      1          quent            0.000
52548      1      nonlinear            0.000
52549      1      mukhwimba            0.000
52550      1   exacerbation            0.000
52551      1      usability            0.000
52552      1        yingtan            0.000
52553      1         palong            0.000

[26277 rows x 3 columns]

epoch                            topic topic_importance
52554      2                           people            0.012
52555      2                         disaster            0.008
52556      2                             corp            0.005
52557      2                             food            0.005
52558      2                            mercy            0.004
52559      2                          society            0.004
52560      2                             year            0.004
52561      2                             need            0.004
52562      2                          country            0.004
52563      2                             mail            0.004
52564      2                          million            0.004
52565      2                           family            0.004
52566      2                            child            0.004
52567      2                    international            0.003
52568      2                        community            0.003
52569      2                             home            0.003
52570      2                            robot            0.003
52571      2                             like            0.003
52572      2                            local            0.003
52573      2                           africa            0.003
52574      2                        emergency            0.003
52575      2                     humanitarian            0.003
52576      2                      information            0.003
52577      2                       government            0.003
52578      2                             help            0.003
52579      2                           relief            0.002
52580      2                         republic            0.002
52581      2                             life            0.002
52582      2                             time            0.002
52583      2                          nuclear            0.002
...      ...                              ...              ...
78801      2                          bristol            0.000
78802      2                         taffesse            0.000
78803      2                        hoddinott            0.000
78804      2                      eradicating            0.000
78805      2  tough_choices_amidst_starvation            0.000
78806      2                            nanda            0.000
78807      2                           moyale            0.000
78808      2                           tibang            0.000
78809      2                 serbiamontenegro            0.000
78810      2                      balochistan            0.000
78811      2                    selfappointed            0.000
78812      2                       overburden            0.000
78813      2                         keystone            0.000
78814      2                          capably            0.000
78815      2                           dinepa            0.000
78816      2                       artibonite            0.000
78817      2                        haitienne            0.000
78818      2                      longlasting            0.000
78819      2                           palace            0.000
78820      2                        policyand            0.000
78821      2                           reused            0.000
78822      2                      reinvention            0.000
78823      2                  nonhumanitarian            0.000
78824      2                         subprime            0.000
78825      2                        austerity            0.000
78826      2                       corpshaiti            0.000
78827      2                      uppermiddle            0.000
78828      2                        postevent            0.000
78829      2                          mayotte            0.000
78830      2                           palong            0.000

[26277 rows x 3 columns]

epoch                  topic topic_importance
78831       3           humanitarian            0.013
78832       3              community            0.012
78833       3             technology            0.009
78834       3                society            0.006
78835       3                 action            0.006
78836       3                  local            0.006
78837       3                   risk            0.006
78838       3                 people            0.006
78839       3              emergency            0.005
78840       3                   need            0.005
78841       3               response            0.005
78842       3                   ifrc            0.005
78843       3              volunteer            0.005
78844       3          international            0.005
78845       3                 mobile            0.005
78846       3               disaster            0.005
78847       3           organization            0.004
78848       3                support            0.004
78849       3                   work            0.004
78850       3               national            0.004
78851       3            information            0.004
78852       3             innovation            0.004
78853       3             government            0.004
78854       3                 social            0.004
78855       3               affected            0.004
78856       3               training            0.004
78857       3              programme            0.003
78858       3                network            0.003
78859       3                service            0.003
78860       3                   help            0.003
...       ...                    ...              ...
105078      3                chiefly            0.000
105079      3               behaving            0.000
105080      3            [millennium            0.000
105081      3             world_camp            0.000
105082      3                uniting            0.000
105083      3                   miti            0.000
105084      3           public_aware            0.000
105085      3                   rcof            0.000
105086      3           exacerbation            0.000
105087      3                  adhoc            0.000
105088      3             _synthesis            0.000
105089      3  _summary_for_decision            0.000
105090      3               mcnaught            0.000
105091      3                 zebiak            0.000
105092      3                  ponzi            0.000
105093      3                daniele            0.000
105094      3                   cies            0.000
105095      3              screwpine            0.000
105096      3               pandanus            0.000
105097      3               permeate            0.000
105098      3             undergoing            0.000
105099      3                  mirna            0.000
105100      3                othowai            0.000
105101      3                abdulla            0.000
105102      3             abdishakur            0.000
105103      3                  quent            0.000
105104      3              nonlinear            0.000
105105      3              mukhwimba            0.000
105106      3              usability            0.000
105107      3                 palong            0.000

[26277 rows x 3 columns]

epoch               topic topic_importance
105108      4        humanitarian            0.013
105109      4          technology            0.009
105110      4         information            0.009
105111      4              people            0.009
105112      4           community            0.007
105113      4             society            0.005
105114      4            disaster            0.005
105115      4                need            0.005
105116      4             country            0.004
105117      4            response            0.004
105118      4              medium            0.004
105119      4       communication            0.004
105120      4             digital            0.004
105121      4              mobile            0.004
105122      4              crisis            0.004
105123      4                many            0.004
105124      4       international            0.004
105125      4        organization            0.004
105126      4               first            0.003
105127      4            affected            0.003
105128      4                risk            0.003
105129      4           volunteer            0.003
105130      4              agency            0.003
105131      4                time            0.003
105132      4                data            0.003
105133      4              system            0.003
105134      4              action            0.003
105135      4              health            0.003
105136      4                ifrc            0.003
105137      4                mail            0.003
...       ...                 ...              ...
131355      4              sismol            0.000
131356      4         prefiguraci            0.000
131357      4             pharoah            0.000
131358      4               parry            0.000
131359      4                olis            0.000
131360      4           occidente            0.000
131361      4  naturalhazardindex            0.000
131362      4              huruma            0.000
131363      4             somsook            0.000
131364      4          regularize            0.000
131365      4         reoccupying            0.000
131366      4              leckie            0.000
131367      4                kerr            0.000
131368      4            arputham            0.000
131369      4                arif            0.000
131370      4            adelekan            0.000
131371      4          expediency            0.000
131372      4      disasterdriven            0.000
131373      4       arbitrariness            0.000
131374      4           ominously            0.000
131375      4         presumption            0.000
131376      4          infeasible            0.000
131377      4           truckload            0.000
131378      4            midnight            0.000
131379      4                lula            0.000
131380      4           doorframe            0.000
131381      4           barricade            0.000
131382      4           approving            0.000
131383      4           memoranda            0.000
131384      4              palong            0.000

[26277 rows x 3 columns]

...

epoch             topic topic_importance
262770     10           society            0.019
262771     10     international            0.016
262772     10              ifrc            0.013
262773     10          national            0.010
262774     10      humanitarian            0.008
262775     10           million            0.007
262776     10        federation            0.007
262777     10            people            0.007
262778     10            online            0.007
262779     10           support            0.007
262780     10          disaster            0.007
262781     10           service            0.006
262782     10         community            0.006
262783     10            annual            0.006
262784     10              http            0.005
262785     10         available            0.005
262786     10             swiss            0.005
262787     10             franc            0.005
262788     10            global            0.005
262789     10              data            0.005
262790     10       development            0.005
262791     10            health            0.005
262792     10          movement            0.005
262793     10            united            0.004
262794     10        government            0.004
262795     10           country            0.004
262796     10         emergency            0.004
262797     10              need            0.004
262798     10          response            0.004
262799     10              year            0.003
...       ...               ...              ...
289017     10           blister            0.000
289018     10       intolerable            0.000
289019     10       translating            0.000
289020     10         closeness            0.000
289021     10              weed            0.000
289022     10       shrivelling            0.000
289023     10           pumpkin            0.000
289024     10          suicidal            0.000
289025     10        germinated            0.000
289026     10         germinate            0.000
289027     10              dull            0.000
289028     10            suckle            0.000
289029     10        sinazongwe            0.000
289030     10              pssa            0.000
289031     10           genital            0.000
289032     10             outed            0.000
289033     10           siamena            0.000
289034     10            howled            0.000
289035     10           titanic            0.000
289036     10          reticent            0.000
289037     10      recalcitrant            0.000
289038     10         precluded            0.000
289039     10        polygamous            0.000
289040     10            jiabao            0.000
289041     10        forthright            0.000
289042     10  fastdisappearing            0.000
289043     10         energized            0.000
289044     10         combative            0.000
289045     10        mutilation            0.000
289046     10            palong            0.000

[26277 rows x 3 columns]

epoch           topic topic_importance
289047     11            http            0.014
289048     11       available            0.010
289049     11          online            0.010
289050     11         written            0.007
289051     11     publication            0.006
289052     11    humanitarian            0.006
289053     11            ifrc            0.005
289054     11        disaster            0.005
289055     11          people            0.005
289056     11   international            0.005
289057     11         society            0.004
289058     11            data            0.004
289059     11          change            0.003
289060     11     development            0.003
289061     11       community            0.003
289062     11         climate            0.003
289063     11     information            0.003
289064     11         refugee            0.003
289065     11       emergency            0.003
289066     11            html            0.003
289067     11         country            0.003
289068     11          global            0.003
289069     11           human            0.003
289070     11          health            0.003
289071     11          crisis            0.002
289072     11        conflict            0.002
289073     11     irevolution            0.002
289074     11           unhcr            0.002
289075     11            need            0.002
289076     11       programme            0.002
...       ...             ...              ...
315294     11       thumbnail            0.000
315295     11        nickname            0.000
315296     11            edit            0.000
315297     11    downloadable            0.000
315298     11  inconsiderable            0.000
315299     11           hyper            0.000
315300     11          giroux            0.000
315301     11        kampfner            0.000
315302     11        flocking            0.000
315303     11        tortoise            0.000
315304     11    responsables            0.000
315305     11     responsable            0.000
315306     11          raketa            0.000
315307     11          projet            0.000
315308     11            mena            0.000
315309     11      immunizing            0.000
315310     11         fencing            0.000
315311     11      gourevitch            0.000
315312     11         dialect            0.000
315313     11        browsing            0.000
315314     11        antibody            0.000
315315     11           isias            0.000
315316     11       corruptly            0.000
315317     11    conciliation            0.000
315318     11         unbound            0.000
315319     11     timesonline            0.000
315320     11          straus            0.000
315321     11         piatkus            0.000
315322     11       custodian            0.000
315323     11          palong            0.000

[26277 rows x 3 columns]

epoch                        topic topic_importance
315324     12                         risk            0.009
315325     12                        urban            0.008
315326     12                    community            0.008
315327     12                     disaster            0.008
315328     12                       people            0.007
315329     12                      country            0.006
315330     12                        local            0.006
315331     12                         city            0.006
315332     12                  development            0.005
315333     12                   government            0.005
315334     12                 humanitarian            0.005
315335     12                        water            0.005
315336     12                         area            0.005
315337     12                  information            0.005
315338     12                     response            0.004
315339     12                         cent            0.004
315340     12                       health            0.004
315341     12                       system            0.004
315342     12                international            0.004
315343     12                     national            0.004
315344     12                   population            0.004
315345     12                       income            0.004
315346     12                         need            0.004
315347     12                         many            0.004
315348     12                        level            0.003
315349     12               infrastructure            0.003
315350     12                    programme            0.003
315351     12                     affected            0.003
315352     12                         time            0.003
315353     12                         data            0.003
...       ...                          ...              ...
341571     12                   alienating            0.000
341572     12                   synonymous            0.000
341573     12                   mj[author]            0.000
341574     12                   schrijvers            0.000
341575     12                 supremecourt            0.000
341576     12                         uksc            0.000
341577     12                        uksc_            0.000
341578     12                    acccessed            0.000
341579     12                         ajph            0.000
341580     12                    etemplate            0.000
341581     12                     saraceno            0.000
341582     12                       saxena            0.000
341583     12                   stormwashi            0.000
341584     12                        unwra            0.000
341585     12                        anshu            0.000
341586     12                      decison            0.000
341587     12        global_health_cluster            0.000
341588     12                     nebraska            0.000
341589     12                       primer            0.000
341590     12                principles_en            0.000
341591     12                  tgdetmenupk            0.000
341592     12                  tgprojdetpk            0.000
341593     12                  tgprojrespk            0.000
341594     12                  tgresmenupk            0.000
341595     12                       thesit            0.000
341596     12          who_constitution_en            0.000
341597     12         yogyakartaprinciples            0.000
341598     12                    stocktake            0.000
341599     12  emergency_respose_framework            0.000
341600     12                      cauthor            0.000

[26277 rows x 3 columns]

epoch                    topic topic_importance
341601     13                     data            0.018
341602     13             humanitarian            0.013
341603     13                 disaster            0.008
341604     13              information            0.008
341605     13                   people            0.008
341606     13               technology            0.007
341607     13                available            0.006
341608     13                  climate            0.006
341609     13                   action            0.005
341610     13                     risk            0.005
341611     13              development            0.005
341612     13                  refugee            0.005
341613     13                   change            0.004
341614     13            international            0.004
341615     13                community            0.004
341616     13                   system            0.004
341617     13                  country            0.004
341618     13                     need            0.004
341619     13                  chapter            0.004
341620     13                    unhcr            0.003
341621     13                     year            0.003
341622     13             displacement            0.003
341623     13               population            0.003
341624     13                emergency            0.003
341625     13                 response            0.003
341626     13                   impact            0.003
341627     13                  project            0.003
341628     13               protection            0.003
341629     13                    human            0.003
341630     13                   online            0.003
...       ...                      ...              ...
367848     13                      wit            0.000
367849     13               penicillin            0.000
367850     13  gppi_urd_cluster_incep_            0.000
367851     13                  lilting            0.000
367852     13                 resupply            0.000
367853     13                 relaxing            0.000
367854     13            unreliability            0.000
367855     13                   magnet            0.000
367856     13                 keystone            0.000
367857     13                  capably            0.000
367858     13                   lentil            0.000
367859     13                 downplay            0.000
367860     13                   dinepa            0.000
367861     13               artibonite            0.000
367862     13                haitienne            0.000
367863     13                hyderabad            0.000
367864     13                  qinghai            0.000
367865     13                 jabalpur            0.000
367866     13                   palace            0.000
367867     13             reconstitute            0.000
367868     13               jamshedpur            0.000
367869     13                 kakinada            0.000
367870     13                swiftness            0.000
367871     13             geologically            0.000
367872     13              kalyanthane            0.000
367873     13                karnataka            0.000
367874     13                 kolhapur            0.000
367875     13                  trebled            0.000
367876     13                 jamnagar            0.000
367877     13                   palong            0.000

[26277 rows x 3 columns]

epoch           topic topic_importance
367878     14          people            0.021
367879     14           total            0.012
367880     14          number            0.010
367881     14         million            0.010
367882     14        disaster            0.009
367883     14    humanitarian            0.008
367884     14        reported            0.008
367885     14            year            0.008
367886     14        affected            0.007
367887     14         country            0.007
367888     14         refugee            0.007
367889     14   international            0.006
367890     14            risk            0.005
367891     14       community            0.005
367892     14     development            0.004
367893     14           unhcr            0.004
367894     14          action            0.004
367895     14    displacement            0.004
367896     14         society            0.004
367897     14      federation            0.004
367898     14            http            0.003
367899     14            data            0.003
367900     14      population            0.003
367901     14          crisis            0.003
367902     14      technology            0.003
367903     14           early            0.003
367904     14        republic            0.003
367905     14          killed            0.003
367906     14   accommodation            0.003
367907     14          global            0.003
...       ...             ...              ...
394125     14          rahine            0.000
394126     14         wherein            0.000
394127     14  simplification            0.000
394128     14   instructional            0.000
394129     14         brimmed            0.000
394130     14        beverage            0.000
394131     14            agba            0.000
394132     14          etikpe            0.000
394133     14  malnourishment            0.000
394134     14          sorgum            0.000
394135     14        ericsson            0.000
394136     14      activating            0.000
394137     14        igniting            0.000
394138     14         telefon            0.000
394139     14           radyo            0.000
394140     14        unveiled            0.000
394141     14    philadelphia            0.000
394142     14       visionary            0.000
394143     14      customised            0.000
394144     14     proficiency            0.000
394145     14      envisioned            0.000
394146     14  federationwide            0.000
394147     14         caicedo            0.000
394148     14        calvario            0.000
394149     14           erazo            0.000
394150     14       jackeline            0.000
394151     14             rio            0.000
394152     14        enhances            0.000
394153     14           noula            0.000
394154     14          palong            0.000

[26277 rows x 3 columns]

In [19]:
common_dictionary.token2id

{'acknow': 0,
 'activity': 1,
 'alleviate': 2,
 'among': 3,
 'analysis': 4,
 'annually': 5,
 'brings': 6,
 'case': 7,
 'cause': 8,
 'center': 9,
 'committee': 10,
 'constitute': 11,
 'contribution': 12,
 'control': 13,
 'coordinating': 14,
 'crisis': 15,
 'detailed': 16,
 'development': 17,
 'difference': 18,
 'disaster': 19,
 'disease': 20,
 'effect': 21,
 'emergency': 22,
 'encouraging': 23,
 'eric': 24,
 'evergrowing': 25,
 'extraordinary': 26,
 'face': 27,
 'fact': 28,
 'federation': 29,
 'field': 30,
 'focus': 31,
 'health': 32,
 'human': 33,
 'humanitarian': 34,
 'indispensable': 35,
 'infectious': 36,
 'information': 37,
 'international': 38,
 'intervention': 39,
 'latest': 40,
 'make': 41,
 'management': 42,
 'movement': 43,
 'multiply': 44,
 'national': 45,
 'noji': 46,
 'partnership': 47,
 'people': 48,
 'preparedness': 49,
 'prevent': 50,
 'prevention': 51,
 'price': 52,
 'promotes': 53,
 'provocative': 54,
 'public': 55,
 'published': 56,
 'recommended': 57,
 'reference': 5

In [18]:
[print(i) for i in common_dictionary.items()]

(0, 'acknow')
(1, 'activity')
(2, 'alleviate')
(3, 'among')
(4, 'analysis')
(5, 'annually')
(6, 'brings')
(7, 'case')
(8, 'cause')
(9, 'center')
(10, 'committee')
(11, 'constitute')
(12, 'contribution')
(13, 'control')
(14, 'coordinating')
(15, 'crisis')
(16, 'detailed')
(17, 'development')
(18, 'difference')
(19, 'disaster')
(20, 'disease')
(21, 'effect')
(22, 'emergency')
(23, 'encouraging')
(24, 'eric')
(25, 'evergrowing')
(26, 'extraordinary')
(27, 'face')
(28, 'fact')
(29, 'federation')
(30, 'field')
(31, 'focus')
(32, 'health')
(33, 'human')
(34, 'humanitarian')
(35, 'indispensable')
(36, 'infectious')
(37, 'information')
(38, 'international')
(39, 'intervention')
(40, 'latest')
(41, 'make')
(42, 'management')
(43, 'movement')
(44, 'multiply')
(45, 'national')
(46, 'noji')
(47, 'partnership')
(48, 'people')
(49, 'preparedness')
(50, 'prevent')
(51, 'prevention')
(52, 'price')
(53, 'promotes')
(54, 'provocative')
(55, 'public')
(56, 'published')
(57, 'recommended')
(58, 'reference

(1754, 'swamping')
(1755, 'tidal')
(1756, 'tube')
(1757, 'animal')
(1758, 'coconut')
(1759, 'corps')
(1760, 'good')
(1761, 'green')
(1762, 'hazard')
(1763, 'littering')
(1764, 'materialized')
(1765, 'nutrient')
(1766, 'predicted')
(1767, 'thought')
(1768, 'valuable')
(1769, 'awareness')
(1770, 'boil')
(1771, 'comprehension')
(1772, 'consumption')
(1773, 'hygiene')
(1774, 'knew')
(1775, 'mobile')
(1776, 'presence')
(1777, 'reinforced')
(1778, 'admission')
(1779, 'bigger')
(1780, 'borne')
(1781, 'certainly')
(1782, 'chemical')
(1783, 'communicable')
(1784, 'considered')
(1785, 'cuttack')
(1786, 'distributed')
(1787, 'halogen')
(1788, 'incidence')
(1789, 'integral')
(1790, 'occurred')
(1791, 'overcrowded')
(1792, 'paradwip')
(1793, 'rapid')
(1794, 'tablet')
(1795, 'undertaken')
(1796, 'unsanitary')
(1797, 'becomes')
(1798, 'fifth')
(1799, 'fragile')
(1800, 'impact')
(1801, 'sell')
(1802, 'serious')
(1803, 'starvation')
(1804, 'survive')
(1805, 'acted')
(1806, 'alleges')
(1807, 'belarusian

(3254, 'performance')
(3255, 'practise')
(3256, 'practising')
(3257, 'prefers')
(3258, 'preliminary')
(3259, 'real')
(3260, 'relationship')
(3261, 'renewed')
(3262, 'respectable')
(3263, 'stage')
(3264, 'statement')
(3265, 'stringent')
(3266, 'vaccinate')
(3267, 'warring')
(3268, 'calm')
(3269, 'career')
(3270, 'dominated')
(3271, 'dwindling')
(3272, 'introduce')
(3273, 'overwhelming')
(3274, 'pervading')
(3275, 'reflection')
(3276, 'rivalry')
(3277, 'turnover')
(3278, 'discus')
(3279, 'learning')
(3280, 'lectureship')
(3281, 'maximize')
(3282, 'prepared')
(3283, 'reflective')
(3284, 'replicated')
(3285, 'stimulating')
(3286, 'debate')
(3287, 'documenting')
(3288, 'dominate')
(3289, 'facilitating')
(3290, 'fail')
(3291, 'formally')
(3292, 'intends')
(3293, 'refinement')
(3294, 'tend')
(3295, 'wrap')
(3296, 'writing')
(3297, 'philanthropist')
(3298, 'strategic')
(3299, 'vaccinated')
(3300, 'always')
(3301, 'build')
(3302, 'contributes')
(3303, 'impression')
(3304, 'inactivity')
(3305, '

(4753, 'noticed')
(4754, 'openness')
(4755, 'understood')
(4756, 'welltrained')
(4757, 'woven')
(4758, 'appointed')
(4759, 'cement')
(4760, 'cloth')
(4761, 'dprkrc')
(4762, 'jrcs')
(4763, 'repatriation')
(4764, 'residing')
(4765, 'rokrc')
(4766, 'round')
(4767, 'sends')
(4768, 'seoul')
(4769, 'successor')
(4770, 'agrees')
(4771, 'construction')
(4772, 'diminishing')
(4773, 'dong')
(4774, 'fire')
(4775, 'fly')
(4776, 'forget')
(4777, 'heart')
(4778, 'hit')
(4779, 'inspect')
(4780, 'inspection')
(4781, 'interfere')
(4782, 'kedo')
(4783, 'peninsula')
(4784, 'reduces')
(4785, 'respectively')
(4786, 'responsible')
(4787, 'taepo')
(4788, 'undated')
(4789, 'undeclared')
(4790, 'underground')
(4791, 'withdraws')
(4792, 'proposed')
(4793, 'track')
(4794, 'advisory')
(4795, 'exceed')
(4796, 'establishes')
(4797, 'italy')
(4798, 'adelphi')
(4799, 'aiden')
(4800, 'array')
(4801, 'article')
(4802, 'book')
(4803, 'button')
(4804, 'carter')
(4805, 'comm')
(4806, 'curie')
(4807, 'dublin')
(4808, 'edge

(6253, 'reminiscent')
(6254, 'sovereign')
(6255, 'spate')
(6256, 'sponsored')
(6257, 'charter')
(6258, 'jurisdiction')
(6259, 'latter')
(6260, 'preconflict')
(6261, 'underscored')
(6262, 'aggression')
(6263, 'authorize')
(6264, 'breach')
(6265, 'accepts')
(6266, 'assertive')
(6267, 'eclipsed')
(6268, 'premise')
(6269, 'arbitrarily')
(6270, 'covenant')
(6271, 'discount')
(6272, 'explicitly')
(6273, 'immigration')
(6274, 'liberty')
(6275, 'lightly')
(6276, 'quarantine')
(6277, 'reasonable')
(6278, 'respected')
(6279, 'scrutiny')
(6280, 'sentence')
(6281, 'shall')
(6282, 'shoulder')
(6283, 'submit')
(6284, 'judgement')
(6285, 'obstructed')
(6286, 'presently')
(6287, 'draft')
(6288, 'exert')
(6289, 'expediting')
(6290, 'milestone')
(6291, 'teeth')
(6292, 'treatise')
(6293, 'undertook')
(6294, 'unitar')
(6295, 'administrative')
(6296, 'attending')
(6297, 'envisioned')
(6298, 'functional')
(6299, 'idndr')
(6300, 'mundane')
(6301, 'parliamentary')
(6302, 'visionary')
(6303, 'privilege')
(6304

...

(21248, 'nominated')
(21249, 'pandanus')
(21250, 'quiz')
(21251, 'screwpine')
(21252, 'nica')
(21253, 'raguan')
(21254, 'agenbox')
(21255, 'napa')
(21256, 'afdb')
(21257, 'cies')
(21258, 'daniele')
(21259, 'ponzi')
(21260, 'climdev')
(21261, 'customized')
(21262, 'zebiak')
(21263, 'mcnaught')
(21264, 'pablo')
(21265, 'agrawala')
(21266, '_summary_for_decision')
(21267, '_synthesis')
(21268, 'adhoc')
(21269, 'bledzki')
(21270, 'ecosystems_and_human_well')
(21271, 'ejournal')
(21272, 'eoearth')
(21273, 'essential_background')
(21274, 'gechs')
(21275, 'hansen')
(21276, 'hellmuth')
(21277, 'menne')
(21278, 'priref')
(21279, 'wellbeing')
(21280, 'halve')
(21281, 'transitory')
(21282, 'apollo')
(21283, 'burditt')
(21284, 'kibet')
(21285, 'ngoleyang')
(21286, 'portending')
(21287, 'sorich')
(21288, 'tonight')
(21289, 'turkana')
(21290, 'mainstay')
(21291, 'buchanansmith')
(21292, 'opti')
(21293, 'changerelated')
(21294, 'wiggins')
(21295, '[such]')
(21296, 'agrhymet')
(21297, 'christopolos')


(22747, 'rover')
(22748, 'sharper')
(22749, 'sincerely')
(22750, 'thunderbird')
(22751, 'interamerican')
(22752, 'montrouis')
(22753, 'annexe')
(22754, 'donald')
(22755, 'kaberuka')
(22756, 'mairie')
(22757, 'twitter')
(22758, 'vilaseau')
(22759, 'ifpri')
(22760, 'beekeeping')
(22761, 'bugiri')
(22762, 'kasasira')
(22763, 'rearing')
(22764, 'rotation')
(22765, 'waiswa')
(22766, 'asturias')
(22767, 'oviedo')
(22768, 'bopha')
(22769, 'commemorated')
(22770, 'flagship')
(22771, 'yabc')
(22772, 'erksoussi')
(22773, 'jaramana')
(22774, 'kahled')
(22775, 'attar')
(22776, 'burkle')
(22777, 'timbuktu')
(22778, 'rahine')
(22779, 'shwe')
(22780, 'dubai')
(22781, 'damango')
(22782, 'fegui')
(22783, 'kayes')
(22784, 'mopti')
(22785, 'moumouni')
(22786, 'leanest')
(22787, 'qqqqq')
(22788, 'qqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqqq')
(22789, 'agba')
(22790, 'etikpe')
(22791, 'malnourishment')
(22792, 'sorgum')
(22793, 'underserved')
(22794, 'phonebased')
(22795, 'qqqqqqqqqqqqqqqqqqq

(24747, 'mediacentre')
(24748, 'mhealth_')
(24749, 'sila')
(24750, 'unfoundation')
(24751, 'communitycentred')
(24752, 'kohut')
(24753, 'meridith')
(24754, 'sahloul')
(24755, 'tutorial')
(24756, 'zaher')
(24757, 'blackout')
(24758, 'mamdouh')
(24759, 'salah')
(24760, 'skype')
(24761, 'gulrukh')
(24762, 'saydia')
(24763, 'testament')
(24764, 'tazreen')
(24765, 'bgmea')
(24766, 'imogen')
(24767, 'amplifying')
(24768, 'infosaid')
(24769, 'wartorn')
(24770, 'truthfully')
(24771, 'abating')
(24772, 'codesheet')
(24773, 'demonstrably')
(24774, 'frontlinesms')
(24775, 'latex')
(24776, 'swahili')
(24777, 'ferocity')
(24778, 'homegrown')
(24779, 'seaboard')
(24780, 'staten')
(24781, 'basement')
(24782, 'borough')
(24783, 'unawares')
(24784, 'queued')
(24785, 'bermudez')
(24786, 'ulyses')
(24787, 'wrecking')
(24788, 'digitally')
(24789, 'iwate')
(24790, 'mediaand')
(24791, 'miyagi')
(24792, 'kyla')
(24793, 'reid')
(24794, 'knafo')
(24795, 'notepad')
(24796, 'rockaways')
(24797, 'occuprint')
(247

(26246, 'zummar')
(26247, 'haut')
(26248, 'kasai')
(26249, '[map')
(26250, 'lusenda')
(26251, 'sote')
(26252, 'brandenburg')
(26253, 'fuerstenwalde')
(26254, 'exiting')
(26255, 'trebling')
(26256, 'vista')
(26257, 'childrenmove')
(26258, 'gambian')
(26259, 'guinean')
(26260, 'capacitate')
(26261, 'capacitation')
(26262, 'definitional')
(26263, 'deportee')
(26264, 'katumba')
(26265, 'lent')
(26266, 'mishamo')
(26267, 'ulyankulu')
(26268, 'yahaya')
(26269, 'idpstat')
(26270, 'refugeestat')
(26271, 'statcom')
(26272, '_external')
(26273, 'tab_v')
(26274, 'hilly')
(26275, 'khali')
(26276, 'palong')


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

## DTM

In [8]:
%%time
home = os.getcwd()

if LOAD_DTM:
    print("loading DTMmodel")
    ldaseq = ldaseqmodel.LdaSeqModel.load('model/DTMmodel_{}'.format(num_topics))
else:
    for num_topics_sub in [5]:
        print("DTMmodel not found; initializing DTMmodel")
        bc = bleicorpus.BleiCorpus.serialize(fname=os.path.join(home, 'model/blei_{}'.format(num_topics_sub)), corpus=common_corpus)
        ldaseq = ldaseqmodel.LdaSeqModel(corpus=common_corpus, id2word=common_dictionary, time_slice=lengths_of_docs, num_topics=num_topics_sub)
        # ldaseq.print_topics(time=0)

        print("saving")
        ldaseq.save(os.path.join(home, 'model/DTMmodel_{}'.format(num_topics_sub)))

DTMmodel not found; initializing DTMmodel


C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

...

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:290: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total)

saving
Wall time: 7h 24min 6s


In [ ]:
def output_dtm_csv():
    '''
    Saves output of DTM as csv
    '''
    with open('dtm_output.csv', 'w', newline='') as f:
        csv_writer = csv.writer(f)
        csv_writer.writerow(['topic', 'time', 'term', 'topic_importance'])
        for t in range(len(lengths_of_docs)):
            counter = 0
            for i in ldaseq.print_topics(time=t, top_terms=15):
        #         print(i)
                counter += 1
                for j in range(len(i)):
                    csv_writer.writerow([counter,t,i[j][0], i[j][1]])

In [ ]:
def display_viz(save = True):
    doc_topic, topic_term, doc_lengths, term_frequency, vocab = ldaseq.dtm_vis(time=0, corpus = common_corpus)
    vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
    if save:
        pyLDAvis.save_html(vis_wrapper, 'viz/DTM{}_viz.html'.format(num_topics))
    else: pass
    return pyLDAvis.display(vis_wrapper)

display_viz()

lambda = 1 results in the familiar ranking of terms in decreasing order of their topic-specific probability, and setting lambda = 0 ranks terms solely by their lift

lift: the ratio of a term’s probability within a topic to its marginal probability across the corpus.

In [ ]:
def plot_specific_topic(term = 'hiv'):
    val_list = []
    for i in ldaseq.print_topic_times(topic=0, top_terms=100):
        for each_tup in i:
            if each_tup[0] == term:
                val_list.append(each_tup[1])
            else: pass
    plt.figure(figsize=(9, 7))
    # plt.title('Scores by group and gender')
    plt.plot(val_list)
    plt.show()

In [ ]:
(train_data, train_targets), (test_data, test_targets) =  boston_housing.load_data()


In [ ]:
mean = train_data.mean(axis=0)
train_data -= mean
std = train_data.std(axis=0)
train_data /= std

test_data -= mean
test_data /= std

In [ ]:
from keras import models
from keras import layers

def build_model():
    # Because we will need to instantiate
    # the same model multiple times,
    # we use a function to construct it.
    model = models.Sequential()
    model.add(layers.Dense(64, activation='relu',
                           input_shape=(train_data.shape[1],)))
    model.add(layers.Dense(64, activation='relu'))
    model.add(layers.Dense(1))
    model.compile(optimizer='rmsprop', loss='mse', metrics=['mae'])
    return model

In [ ]:
import numpy as np

k = 4
num_val_samples = len(train_data) // k
num_epochs = 100
all_scores = []
for i in range(k):
    print('processing fold #', i)
    # Prepare the validation data: data from partition # k
    val_data = train_data[i * num_val_samples: (i + 1) * num_val_samples]
    val_targets = train_targets[i * num_val_samples: (i + 1) * num_val_samples]

    # Prepare the training data: data from all other partitions
    partial_train_data = np.concatenate(
        [train_data[:i * num_val_samples],
         train_data[(i + 1) * num_val_samples:]],
        axis=0)
    partial_train_targets = np.concatenate(
        [train_targets[:i * num_val_samples],
         train_targets[(i + 1) * num_val_samples:]],
        axis=0)

    # Build the Keras model (already compiled)
    model = build_model()
    # Train the model (in silent mode, verbose=0)
    model.fit(partial_train_data, partial_train_targets,
              epochs=num_epochs, batch_size=1, verbose=0)
    # Evaluate the model on the validation data
    val_mse, val_mae = model.evaluate(val_data, val_targets, verbose=0)
    all_scores.append(val_mae)
    
all_scores

In [ ]:
# Get a fresh, compiled model.
model = build_model()
# Train it on the entirety of the data.
model.fit(train_data, train_targets,
          epochs=80, batch_size=16, verbose=0)
test_mse_score, test_mae_score = model.evaluate(test_data, test_targets)
print(test_mae_score)